# Préambule : nos biais inconscients

Nous vous proposons, si vous le souhaitez, de prendre une dizaine de minutes pour tester vos biais inconscients:

https://implicit.harvard.edu/implicit/canadafr/takeatest.html


# TD 2: Manipulation des données

As a best practice, please use a virtual environment following the step explained here
[python virtual env](https://ecampus.paris-saclay.fr/pluginfile.php/3606005/mod_folder/content/0/installation.md?forcedownload=1)

```
numpy==1.25
fairlearn==0.9.0
plotly==5.24.1
nbformat==5.10.4
ipykernel==6.29.5
aif360['inFairness']==0.6.1
causal-learn==0.1.4.0
```


You with also need to have R installed 
`sudo apt install r-base-core`

In this TD we will use data from the [Medical Expenditure Panel Survey](https://meps.ahrq.gov/mepsweb/). The TD is inspired from [AIF360 tutorial](https://github.com/Trusted-AI/AIF360/blob/main/examples/tutorial_medical_expenditure.ipynb)

## Download the dataset

Use the command lines below, if you encounter a problem do not hesitate to call for help

``` 
python_bin_path="$(which python)"; \
meps_path="$(dirname $python_bin_path})"; \
cd $meps_path; \
cd ../lib/python3.10/site-packages/aif360/data/raw/meps; \
Rscript generate_data.R
```

It will ask to read the rules and restrictions to download and use this dataset.
This is because the dataset is a medical dataset witl real person information.

The download can take a bit of time

In [1]:
# imports
import numpy as np
import pandas as pd
import plotly.express as px
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.simplefilter(action='ignore', append=True, category=UserWarning)


In [3]:
# Datasets
from aif360.datasets import MEPSDataset19
from aif360.datasets import MEPSDataset20
from aif360.datasets import MEPSDataset21

MEPSDataset19_data = MEPSDataset19()

In [4]:
(dataset_orig_panel19_train,
 dataset_orig_panel19_val,
 dataset_orig_panel19_test) = MEPSDataset19().split([0.5, 0.8], shuffle=True)

In [5]:
len(dataset_orig_panel19_train.instance_weights), len(dataset_orig_panel19_val.instance_weights), len(dataset_orig_panel19_test.instance_weights)

(7915, 4749, 3166)

Nous vous conseillons d'aller voir les pages  [MEPSDataset19](https://aif360.readthedocs.io/en/latest/modules/generated/aif360.datasets.MEPSDataset19.html) et [AIF360 tutorial](https://github.com/Trusted-AI/AIF360/blob/main/examples/tutorial_medical_expenditure.ipynb) pour mieux comprendre le dataset.

Ce qu'il faut avoir lu:
- **The sensitive attribute is 'RACE' :1 is privileged, 0 is unprivileged** ; It is constructed as follows: 'Whites' (privileged class) defined by the features RACEV2X = 1 (White) and HISPANX = 2 (non Hispanic); 'Non-Whites' that included everyone else.
(The features 'RACEV2X', 'HISPANX' etc are removed, and replaced by the 'RACE')
- **'UTILIZATION' is the outcome (the label to predict for a ML model) 0 is positive 1 is negative**. It is a binary composite feature, created to measure the total number of trips requiring some sort of medical care, it sum up the following features (that are removed from the data):
    * OBTOTV15(16), the number of office based visits
    * OPTOTV15(16), the number of outpatient visits
    * ERTOT15(16), the number of ER visits
    * IPNGTD15(16), the number of inpatient nights
    * HHTOTD16, the number of home health visits
UTILISATION is set to 1 when te sum is above or equal to 10, else it is set to 0
- **The dataset is weighted** The dataset come with an 'instance_weights' attribute that corresponds to the feature perwt15f these weights are supposed to generate estimates that are representative of the United State (US) population in 2015.


Ce qu'il faut avoir retenu:
- **The sensitive attribute is 'RACE' :1 is privileged, 0 is unprivileged**
- **'UTILIZATION' is the outcome (the label to predict for a ML model) 0 is positive 1 is negative**
- **The dataset is weighted**



In [6]:
instance_weights = MEPSDataset19_data.instance_weights
instance_weights


array([21854.981705, 18169.604822, 17191.832515, ...,  3896.116219,
        4883.851005,  6630.588948])

In [7]:
f"Taille du dataset {len(instance_weights)}, poids total du dataset {instance_weights.sum()}."

'Taille du dataset 15830, poids total du dataset 141367240.546316.'

### Premier appercu du dataset

La librairie AIF360 fournie une surcouche au dataset, cela le rend un peu moins intuitif d'utilisation (par exemple pour étudier/visualiser les attributs un à un), mais elle permet de calculer les métrique des fairness en une ligne de commande.

In [8]:
from aif360.metrics import BinaryLabelDatasetMetric
from aif360.metrics import ClassificationMetric

metric_orig_panel19_train = BinaryLabelDatasetMetric(
        MEPSDataset19_data,
        unprivileged_groups=[{'RACE': 0}],
        privileged_groups=[{'RACE': 1}])

print(metric_orig_panel19_train.disparate_impact())

pip install 'aif360[AdversarialDebiasing]'
pip install 'aif360[AdversarialDebiasing]'


0.49826823461176517


Cependant le but de ce TD étant encore de manipuler les données et de les analyser nous allons revenir aux données sous forme d'un dataframe.

Note pour calculer les métriques de fairness sans avoir à les réimplémenter dans le cas pondéré (instances weights) vous pouvez utiliser les méthodes implémenter dans AIF360 là [Implémentation Métriques de Fairness](https://aif360.readthedocs.io/en/latest/modules/sklearn.html#module-aif360.sklearn.metrics)

### Conversion en un dataframe

Nous avons vu que la somme des poids est conséquente, pres de 115millions nous ne pouvons donc pas raisonneblement dupliqué chaque ligne autant de fois que son poids.

Nous allons stocker la pondération et la prendre en compte ensuite dans notre analyse

In [9]:
def get_df(MepsDataset):
    data = MepsDataset.convert_to_dataframe()
    # data_train est un tuple, avec le data_frame et un dictionnaire avec toutes les infos (poids, attributs sensibles etc)
    df = data[0]
    df['WEIGHT'] = data[1]['instance_weights']
    return df

df = get_df(MEPSDataset19_data)



In [10]:
from aif360.sklearn.metrics import disparate_impact_ratio, base_rate
dir = disparate_impact_ratio(
    y_true=df.UTILIZATION, 
    prot_attr=df.RACE, 
    pos_label=0,
    sample_weight=df.WEIGHT)
br =base_rate(
    y_true=df.UTILIZATION, 
    pos_label=0,
    sample_weight=df.WEIGHT)
dir,br

(1.1848351529675123, 0.7849286063696154)

In [11]:
dir = disparate_impact_ratio(
    y_true=df.UTILIZATION, 
    prot_attr=df.RACE, 
    pos_label=0)
br =base_rate(
    y_true=df.UTILIZATION, 
    pos_label=0)
dir,br

(1.1746792888264614, 0.8283006948831333)

## Question 1 - Apprendre un modèle pour prédire le fait d'être réadmis
### 1.1 - Faire le pre-processing des données

Ici ce pre-processing a déjà été fait par AIF, nous avons simplement converti le dataset en dataframe pour pouvoir le manipuler librement

### Question 1.2 - Creer les échantillons d'apprentissage, de validation et de test

Pour créer le df_X il faut enlever l'outcome ("UTILIZATION") et la pondération ("WEIGHT")

La colonne "UTILIZATION" sera le label (noté y)

La colonne "WEIGHT" sera la pondération (notée w)


In [12]:
from sklearn.model_selection import train_test_split
df_X = df.drop(columns=["UTILIZATION", "WEIGHT"])
splits_trainval_test = train_test_split(
    df_X, df["UTILIZATION"], df["WEIGHT"],
    train_size=0.8, 
    random_state=42)

X_trainval, X_test, y_trainval, y_test, w_trainval, w_test = splits_trainval_test
splits_train_val = train_test_split(
    X_trainval, y_trainval, w_trainval,
    train_size=0.625, 
    random_state=42)
X_train, X_val, y_train, y_val, w_train, w_val = splits_train_val

In [13]:
X_train.shape, y_train.shape, w_train.shape, X_val.shape, y_val.shape, w_val.shape,  X_test.shape, y_test.shape, w_test.shape

((7915, 138),
 (7915,),
 (7915,),
 (4749, 138),
 (4749,),
 (4749,),
 (3166, 138),
 (3166,),
 (3166,))

### Question 1.3 - Apprendre une regression logistique dont le but est de prédire UTILIZATION

In [14]:
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import make_pipeline


model = make_pipeline(StandardScaler(),LogisticRegression(random_state=42))

model = model.fit(X_train, y_train, **{'logisticregression__sample_weight':w_train})

preds = model.predict(X_val)

model.score(X_val, y_val, sample_weight=w_val)

0.8429447781148914

### Quesiton 1.4 Performance du modèle (afficher la matrice de confusion)

In [15]:
from sklearn.metrics import confusion_matrix
tn, fp, fn, tp = confusion_matrix(y_val, preds).ravel()
print(tn, fp, fn, tp)
fig = px.imshow([[tn, fp], [fn, tp]], text_auto=True, labels=dict(y="Truth", x="Pred"),
                x=["False", "True"],
                y=["False", "True"]
               )
fig.show()

3773 176 456 344


### Question 1.5 - Calculer les métriques "group fairness" du modèle

In [16]:
from aif360.sklearn.metrics import *

def get_group_metrics(args):
    # args : dic with value y_true, y_pred, prot_attr, priv_group, pos_labl, sample_weight
    group_metrics={}
    group_metrics["statistical_parity_difference"]=statistical_parity_difference(**args)
    group_metrics["disparate_impact_ratio"]=disparate_impact_ratio(**args)
    group_metrics["equal_opportunity_difference"]=equal_opportunity_difference(**args)
    group_metrics["average_odds_difference"]=average_odds_difference(**args)
    group_metrics["conditional_demographic_disparity"]=conditional_demographic_disparity(**args)
    group_metrics["smoothed_edf"]=smoothed_edf(**args)
    group_metrics["df_bias_amplification"]=df_bias_amplification(**args)
    return group_metrics



group_metrics = get_group_metrics( {
    "y_true": y_val,
    "y_pred": y_val,
    "prot_attr": X_val["RACE"], 
    "pos_label":0,
    "sample_weight":w_val
    })
group_metrics

{'statistical_parity_difference': 0.14593258594320302,
 'disparate_impact_ratio': 1.2014878422901056,
 'equal_opportunity_difference': 0.0,
 'average_odds_difference': 0.0,
 'conditional_demographic_disparity': 0.041588573541055184,
 'smoothed_edf': 0.7534670691209806,
 'df_bias_amplification': 0.0}

In [17]:
# Métriques du modèle avec pondération
model_group_metrics = get_group_metrics( {
    "y_true": y_val,
    "y_pred": preds,
    "prot_attr": X_val["RACE"], 
    "pos_label":0,
    "sample_weight":w_val
    }
)
model_group_metrics

{'statistical_parity_difference': 0.1293902930520614,
 'disparate_impact_ratio': 1.1607532512503969,
 'equal_opportunity_difference': 0.045029230285676736,
 'average_odds_difference': 0.12112029660569726,
 'conditional_demographic_disparity': 0.051066340714915316,
 'smoothed_edf': 1.0882653239012994,
 'df_bias_amplification': 0.33479825478031877}

In [18]:
# Métriques du modèle sans pondération
model_group_metrics = get_group_metrics( {
    "y_true": y_val,
    "y_pred": preds,
    "prot_attr": X_val["RACE"], 
    "pos_label":0,
    }
)
model_group_metrics

{'statistical_parity_difference': 0.11807222130273276,
 'disparate_impact_ratio': 1.144803973322301,
 'equal_opportunity_difference': 0.050159825475247444,
 'average_odds_difference': 0.09885624903454635,
 'conditional_demographic_disparity': -0.07631282373628226,
 'smoothed_edf': 1.0193435495802454,
 'df_bias_amplification': 0.2655922169044387}

## Question 2 - Etude de l'impact de la couleur de peau sur le faire d'être réadmis, les prédictions du modèle et ses liens avec les autres variables


### Question 2.1 - Faire l'étude descriptive univarié de la couleur de peau ('RACE') (effectif, fréquence, model)

### Question 2.2 - Faire des graphiques décrivant la couleur de peau  (diagramme en secteur, diagramme en barres)

### Question 2.3 - Faire l'analyse bivariée entre la couleur de peau et les autres variables explicatives quantitatives (boite à moustaches des variables par genre, densité/histogramme par genre, rapport de corrélation)

### Question 2.4 - Faire l'analyse bivariée entre la couelur de peau et d'autres variables explicatives qualitative (table de contingence, diagramme en barre selon les profils lignes et selon les profils colonnes, diagramme en mosaique)

### Question 2.5 - Faire l'analyse bivariée entre la couleur de peau et la colonne 'UTILIZATION'

### Question 2.6 - Faire l'analyse bivariée entre la couleur de peau et les prédictions du modèle prédisant la colonne 'UTILIZATION'

### Question 2.7 - Faire l'analyse bivariée entre la couleur de peau et les erreurs du modèle précédent

### Question 2.8 - Proposer un modèle à base d'une foret aléatoire prédisant la couleur de peau en fonction des autres variables explicatives

### Question 2.9 - Apprendre un modèle privé de la couleur de peau pour prédire UTILIZATION et étudier le lien entre ses prédictions et la couleur de peau

## Question 3 - Faire de meme pour une autre variable sensible (Age, genre, marry etc)


## Question 4 - Causalité: appliquer le module causal-learn sur le jeu de données en testant plusieurs des méthodes implémentées et en comparant les résultats entre les méthodes